In [15]:
# !pip install -r ./requirements.txt

In [2]:
# !pip uninstall virny -y

In [4]:
# Install using an HTTP link
# !pip install git+https://github.com/DataResponsibly/Virny.git@feature/prepare_experiments_for_inprocessors

# Install using an SSH link
# !pip install git+ssh://git@github.com/DataResponsibly/Virny.git@feature/prepare_experiments_for_inprocessors

In [1]:
%matplotlib inline
%load_ext autoreload
%autoreload 2

In [2]:
import os
import warnings
warnings.filterwarnings('ignore')
os.environ["PYTHONWARNINGS"] = "ignore"

In [3]:
cur_folder_name = os.getcwd().split('/')[-1]
if cur_folder_name != "fairness-variance":
    os.chdir("../../../..")

print('Current location: ', os.getcwd())

Current location:  /home/dh3553/projects/fairness-variance


## Import dependencies

In [4]:
import copy

from virny.utils.custom_initializers import create_config_obj
from virny.datasets import LawSchoolDataset

from configs.constants import TEST_SET_FRACTION, EXPERIMENT_SEEDS

from source.experiment_interface import run_exp_iter_with_inprocessor

pip install 'aif360[LawSchoolGPA]'
pip install 'aif360[Reductions]'
pip install 'aif360[Reductions]'
pip install 'aif360[Reductions]'


## Define Input Variables

In [5]:
ROOT_DIR = os.getcwd()
EXPERIMENT_NAME = 'ADB_law_school'
DB_COLLECTION_NAME = 'one_repair_lvl_many_models'
FAIRNESS_INTERVENTION_NAME = 'ADB'
FAIR_INTERVENTION_PARAMS_LST = ['debiased_classifier']
SAVE_RESULTS_DIR_PATH = os.path.join(ROOT_DIR, 'results', 'diff_fairness_interventions_exp',
                                     FAIRNESS_INTERVENTION_NAME, EXPERIMENT_NAME)

config_yaml_path = os.path.join(ROOT_DIR, 'notebooks', 'diff_fairness_interventions_exp',
                                FAIRNESS_INTERVENTION_NAME, EXPERIMENT_NAME, 'law_school_config.yaml')
metrics_computation_config = create_config_obj(config_yaml_path=config_yaml_path)

## Define a db writer and custom fields to insert into your database

In [6]:
import os
from dotenv import load_dotenv

load_dotenv('./configs/secrets.env')
os.getenv("DB_NAME")

'fairness_variance'

In [7]:
from source.utils.db_functions import connect_to_mongodb

client, collection_obj, db_writer_func = connect_to_mongodb(DB_COLLECTION_NAME)

In [8]:
import uuid

custom_table_fields_dct = {
#     'session_uuid': str(uuid.uuid4()),
    'session_uuid': '594152d2-738f-43f3-87ac-e98b98a17b4a',
}
print('Current session uuid: ', custom_table_fields_dct['session_uuid'])

Current session uuid:  594152d2-738f-43f3-87ac-e98b98a17b4a


## Initialize custom objects

In [9]:
data_loader = LawSchoolDataset()
data_loader.X_data.head()

decile1b  decile3  lsat  ugpa  zfygpa  zgpa fulltime fam_inc male tier  \
0      10.0     10.0  44.0   3.5    1.33  1.88      1.0     5.0  0.0  4.0   
1       5.0      4.0  29.0   3.5   -0.11 -0.57      1.0     4.0  0.0  2.0   
2       8.0      7.0  37.0   3.4    0.63  0.37      1.0     3.0  1.0  4.0   
3       8.0      7.0  43.0   3.3    0.67  0.34      1.0     4.0  0.0  4.0   
4       3.0      2.0  41.0   3.3   -0.67 -1.30      1.0     4.0  0.0  5.0   

    race  
0  White  
1  White  
2  White  
3  White  
4  White

In [10]:
data_loader.X_data.shape

(20798, 11)

## Run experiment iterations

### Experiment iteration 1

In [14]:
# Configs for an experiment iteration
exp_iter_num = 1
experiment_seed = EXPERIMENT_SEEDS[exp_iter_num - 1]
custom_table_fields_dct['experiment_iteration'] = f'Exp_iter_{exp_iter_num}'
exp_iter_data_loader = copy.deepcopy(data_loader)  # Add deepcopy to avoid data leakage

In [ ]:
run_exp_iter_with_inprocessor(data_loader=exp_iter_data_loader,
                              experiment_seed=experiment_seed,
                              test_set_fraction=TEST_SET_FRACTION,
                              db_writer_func=db_writer_func,
                              fair_intervention_params_lst=FAIR_INTERVENTION_PARAMS_LST,
                              metrics_computation_config=metrics_computation_config,
                              custom_table_fields_dct=custom_table_fields_dct,
                              dataset_name='LawSchoolDataset',
                              inprocessor_name='AdversarialDebiasing',
                              verbose=True)

2024-01-08 20:48:27 experiment_interface.py INFO    : Start an experiment iteration for the following custom params:
INFO:root:Start an experiment iteration for the following custom params:


{'dataset_split_seed': 100,
 'experiment_iteration': 'Exp_iter_1',
 'fair_intervention_params_lst': "['debiased_classifier']",
 'model_init_seed': 100,
 'session_uuid': '594152d2-738f-43f3-87ac-e98b98a17b4a'}




Multiple alphas:   0%|          | 0/1 [00:00<?, ?it/s]

2024-01-08 20:48:27 experiment_interface.py INFO    : The dataset is preprocessed
INFO:root:The dataset is preprocessed


intervention_option:  debiased_classifier
cur_base_flow_dataset.X_train_val.columns:  Index(['cat__fulltime_1.0', 'cat__fulltime_2.0', 'cat__fam_inc_1.0',
       'cat__fam_inc_2.0', 'cat__fam_inc_3.0', 'cat__fam_inc_4.0',
       'cat__fam_inc_5.0', 'cat__tier_1.0', 'cat__tier_2.0', 'cat__tier_3.0',
       'cat__tier_4.0', 'cat__tier_5.0', 'cat__tier_6.0', 'num__decile1b',
       'num__decile3', 'num__lsat', 'num__ugpa', 'num__zfygpa', 'num__zgpa',
       'male&race_binary'],
      dtype='object')
Top indexes of an X_test in the current base flow dataset:  Int64Index([ 7102,   593, 18841,  5078, 14172,  8064, 13554, 13401, 17015,
            18446,  6938,  3450,  9375, 19994, 16100,  4401,   142, 15143,
             2188,  4332],
           dtype='int64')
Top indexes of an y_test in the current base flow dataset:  Int64Index([ 7102,   593, 18841,  5078, 14172,  8064, 13554, 13401, 17015,
            18446,  6938,  3450,  9375, 19994, 16100,  4401,   142, 15143,
             2188,  4332]

...

epoch 126; iter: 0; batch classifier loss: 0.237986; batch adversarial loss: 0.236680
epoch 127; iter: 0; batch classifier loss: 0.178301; batch adversarial loss: 0.267195
epoch 128; iter: 0; batch classifier loss: 0.234951; batch adversarial loss: 0.216251
epoch 129; iter: 0; batch classifier loss: 0.232502; batch adversarial loss: 0.181960
epoch 130; iter: 0; batch classifier loss: 0.174061; batch adversarial loss: 0.249352
epoch 131; iter: 0; batch classifier loss: 0.207908; batch adversarial loss: 0.231062
epoch 132; iter: 0; batch classifier loss: 0.194231; batch adversarial loss: 0.312160
epoch 133; iter: 0; batch classifier loss: 0.191275; batch adversarial loss: 0.318008
epoch 134; iter: 0; batch classifier loss: 0.275554; batch adversarial loss: 0.233308
epoch 135; iter: 0; batch classifier loss: 0.151887; batch adversarial loss: 0.205730
epoch 136; iter: 0; batch classifier loss: 0.221367; batch adversarial loss: 0.236203
epoch 137; iter: 0; batch classifier loss: 0.223610; b

epoch 22; iter: 0; batch classifier loss: 0.228222; batch adversarial loss: 0.302106
epoch 23; iter: 0; batch classifier loss: 0.220937; batch adversarial loss: 0.214815
epoch 24; iter: 0; batch classifier loss: 0.206582; batch adversarial loss: 0.237826
epoch 25; iter: 0; batch classifier loss: 0.254610; batch adversarial loss: 0.255199
epoch 26; iter: 0; batch classifier loss: 0.334749; batch adversarial loss: 0.243187
epoch 27; iter: 0; batch classifier loss: 0.218630; batch adversarial loss: 0.238284
epoch 28; iter: 0; batch classifier loss: 0.164350; batch adversarial loss: 0.300537
epoch 29; iter: 0; batch classifier loss: 0.225102; batch adversarial loss: 0.177948
epoch 30; iter: 0; batch classifier loss: 0.262574; batch adversarial loss: 0.255589
epoch 31; iter: 0; batch classifier loss: 0.180076; batch adversarial loss: 0.276128
epoch 32; iter: 0; batch classifier loss: 0.261940; batch adversarial loss: 0.139408
epoch 33; iter: 0; batch classifier loss: 0.226447; batch adversa

epoch 120; iter: 0; batch classifier loss: 0.205390; batch adversarial loss: 0.265674
epoch 121; iter: 0; batch classifier loss: 0.188905; batch adversarial loss: 0.247095
epoch 122; iter: 0; batch classifier loss: 0.182947; batch adversarial loss: 0.304027
epoch 123; iter: 0; batch classifier loss: 0.172584; batch adversarial loss: 0.333531
epoch 124; iter: 0; batch classifier loss: 0.136055; batch adversarial loss: 0.301709
epoch 125; iter: 0; batch classifier loss: 0.160513; batch adversarial loss: 0.228646
epoch 126; iter: 0; batch classifier loss: 0.187211; batch adversarial loss: 0.232823
epoch 127; iter: 0; batch classifier loss: 0.197737; batch adversarial loss: 0.155951
epoch 128; iter: 0; batch classifier loss: 0.163900; batch adversarial loss: 0.208353
epoch 129; iter: 0; batch classifier loss: 0.214634; batch adversarial loss: 0.301492
epoch 130; iter: 0; batch classifier loss: 0.259555; batch adversarial loss: 0.257223
epoch 131; iter: 0; batch classifier loss: 0.124308; b

epoch 16; iter: 0; batch classifier loss: 0.143163; batch adversarial loss: 0.248591
epoch 17; iter: 0; batch classifier loss: 0.125614; batch adversarial loss: 0.236679
epoch 18; iter: 0; batch classifier loss: 0.251560; batch adversarial loss: 0.260451
epoch 19; iter: 0; batch classifier loss: 0.212789; batch adversarial loss: 0.259844
epoch 20; iter: 0; batch classifier loss: 0.306934; batch adversarial loss: 0.221403
epoch 21; iter: 0; batch classifier loss: 0.232019; batch adversarial loss: 0.276075
epoch 22; iter: 0; batch classifier loss: 0.180512; batch adversarial loss: 0.240090
epoch 23; iter: 0; batch classifier loss: 0.179178; batch adversarial loss: 0.154549
epoch 24; iter: 0; batch classifier loss: 0.182773; batch adversarial loss: 0.304362
epoch 25; iter: 0; batch classifier loss: 0.238138; batch adversarial loss: 0.255670
epoch 26; iter: 0; batch classifier loss: 0.251815; batch adversarial loss: 0.237885
epoch 27; iter: 0; batch classifier loss: 0.199754; batch adversa

epoch 114; iter: 0; batch classifier loss: 0.219859; batch adversarial loss: 0.358884
epoch 115; iter: 0; batch classifier loss: 0.215945; batch adversarial loss: 0.219793
epoch 116; iter: 0; batch classifier loss: 0.164803; batch adversarial loss: 0.208779
epoch 117; iter: 0; batch classifier loss: 0.206981; batch adversarial loss: 0.294057
epoch 118; iter: 0; batch classifier loss: 0.287486; batch adversarial loss: 0.246568
epoch 119; iter: 0; batch classifier loss: 0.145147; batch adversarial loss: 0.193627
epoch 120; iter: 0; batch classifier loss: 0.206984; batch adversarial loss: 0.313317
epoch 121; iter: 0; batch classifier loss: 0.162608; batch adversarial loss: 0.262507
epoch 122; iter: 0; batch classifier loss: 0.200982; batch adversarial loss: 0.299336
epoch 123; iter: 0; batch classifier loss: 0.196768; batch adversarial loss: 0.251267
epoch 124; iter: 0; batch classifier loss: 0.214122; batch adversarial loss: 0.234994
epoch 125; iter: 0; batch classifier loss: 0.222435; b

### Experiment iteration 2

In [4]:
# Configs for an experiment iteration
exp_iter_num = 2
experiment_seed = EXPERIMENT_SEEDS[exp_iter_num - 1]
custom_table_fields_dct['experiment_iteration'] = f'Exp_iter_{exp_iter_num}'
exp_iter_data_loader = copy.deepcopy(data_loader)  # Add deepcopy to avoid data leakage

NameError: name 'EXPERIMENT_SEEDS' is not defined

In [21]:
run_exp_iter_with_inprocessor(data_loader=exp_iter_data_loader,
                              experiment_seed=experiment_seed,
                              test_set_fraction=TEST_SET_FRACTION,
                              db_writer_func=db_writer_func,
                              fair_intervention_params_lst=FAIR_INTERVENTION_PARAMS_LST,
                              metrics_computation_config=metrics_computation_config,
                              custom_table_fields_dct=custom_table_fields_dct,
                              dataset_name='LawSchoolDataset',
                              inprocessor_name='AdversarialDebiasing',
                              verbose=True)

2024-01-04 17:15:39 experiment_interface.py INFO    : Start an experiment iteration for the following custom params:
INFO:root:Start an experiment iteration for the following custom params:


{'dataset_split_seed': 200,
 'experiment_iteration': 'Exp_iter_2',
 'fair_intervention_params_lst': '[True]',
 'intervention_param': 'True',
 'model_init_seed': 200,
 'session_uuid': '0626d80f-e288-4f16-b8ab-260eb34d62d3'}


Multiple alphas:   0%|          | 0/1 [00:00<?, ?it/s]

2024-01-04 17:15:39 experiment_interface.py INFO    : The dataset is preprocessed
INFO:root:The dataset is preprocessed
2024-01-04 17:15:39 experiment_interface.py INFO    : Models config is loaded from the input file
INFO:root:Models config is loaded from the input file


intervention_option:  True
Using ROC postprocessor
cur_base_flow_dataset.X_train_val.columns:  Index(['cat__school_GP', 'cat__school_MS', 'cat__address_R', 'cat__address_U',
       'cat__famsize_GT3', 'cat__famsize_LE3', 'cat__Pstatus_A',
       'cat__Pstatus_T', 'cat__Mjob_at_home', 'cat__Mjob_health',
       'cat__Mjob_other', 'cat__Mjob_services', 'cat__Mjob_teacher',
       'cat__Fjob_at_home', 'cat__Fjob_health', 'cat__Fjob_other',
       'cat__Fjob_services', 'cat__Fjob_teacher', 'cat__reason_course',
       'cat__reason_home', 'cat__reason_other', 'cat__reason_reputation',
       'cat__guardian_father', 'cat__guardian_mother', 'cat__guardian_other',
       'cat__schoolsup_no', 'cat__schoolsup_yes', 'cat__famsup_no',
       'cat__famsup_yes', 'cat__paid_no', 'cat__paid_yes',
       'cat__activities_no', 'cat__activities_yes', 'cat__nursery_no',
       'cat__nursery_yes', 'cat__higher_no', 'cat__higher_yes',
       'cat__internet_no', 'cat__internet_yes', 'cat__romantic_no',
     

...

[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGB

[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGB

Classifiers testing by bootstrap:   0%|          | 0/200 [00:00<?, ?it/s]

Enabled a postprocessing mode


Classifiers testing by bootstrap:   0%|          | 0/200 [00:00<?, ?it/s]

### Experiment iteration 3

In [11]:
# Configs for an experiment iteration
exp_iter_num = 3
experiment_seed = EXPERIMENT_SEEDS[exp_iter_num - 1]
custom_table_fields_dct['experiment_iteration'] = f'Exp_iter_{exp_iter_num}'
exp_iter_data_loader = copy.deepcopy(data_loader)  # Add deepcopy to avoid data leakage

In [12]:
run_exp_iter_with_inprocessor(data_loader=exp_iter_data_loader,
                              experiment_seed=experiment_seed,
                              test_set_fraction=TEST_SET_FRACTION,
                              db_writer_func=db_writer_func,
                              fair_intervention_params_lst=FAIR_INTERVENTION_PARAMS_LST,
                              metrics_computation_config=metrics_computation_config,
                              custom_table_fields_dct=custom_table_fields_dct,
                              dataset_name='LawSchoolDataset',
                              inprocessor_name='AdversarialDebiasing',
                              verbose=True)

2024-01-04 19:29:01 experiment_interface.py INFO    : Start an experiment iteration for the following custom params:
INFO:root:Start an experiment iteration for the following custom params:


{'dataset_split_seed': 300,
 'experiment_iteration': 'Exp_iter_3',
 'fair_intervention_params_lst': '[True]',
 'model_init_seed': 300,
 'session_uuid': '0626d80f-e288-4f16-b8ab-260eb34d62d3'}


Multiple alphas:   0%|          | 0/1 [00:00<?, ?it/s]

2024-01-04 19:29:01 experiment_interface.py INFO    : The dataset is preprocessed
INFO:root:The dataset is preprocessed
2024-01-04 19:29:01 experiment_interface.py INFO    : Models config is loaded from the input file
INFO:root:Models config is loaded from the input file


intervention_option:  True
Using ROC postprocessor
cur_base_flow_dataset.X_train_val.columns:  Index(['cat__school_GP', 'cat__school_MS', 'cat__address_R', 'cat__address_U',
       'cat__famsize_GT3', 'cat__famsize_LE3', 'cat__Pstatus_A',
       'cat__Pstatus_T', 'cat__Mjob_at_home', 'cat__Mjob_health',
       'cat__Mjob_other', 'cat__Mjob_services', 'cat__Mjob_teacher',
       'cat__Fjob_at_home', 'cat__Fjob_health', 'cat__Fjob_other',
       'cat__Fjob_services', 'cat__Fjob_teacher', 'cat__reason_course',
       'cat__reason_home', 'cat__reason_other', 'cat__reason_reputation',
       'cat__guardian_father', 'cat__guardian_mother', 'cat__guardian_other',
       'cat__schoolsup_no', 'cat__schoolsup_yes', 'cat__famsup_no',
       'cat__famsup_yes', 'cat__paid_no', 'cat__paid_yes',
       'cat__activities_no', 'cat__activities_yes', 'cat__nursery_no',
       'cat__nursery_yes', 'cat__higher_no', 'cat__higher_yes',
       'cat__internet_no', 'cat__internet_yes', 'cat__romantic_no',
     

...

[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGB

[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGB

Classifiers testing by bootstrap:   0%|          | 0/200 [00:00<?, ?it/s]

Enabled a postprocessing mode


Classifiers testing by bootstrap:   0%|          | 0/200 [00:00<?, ?it/s]

### Experiment iteration 4

In [13]:
# Configs for an experiment iteration
exp_iter_num = 4
experiment_seed = EXPERIMENT_SEEDS[exp_iter_num - 1]
custom_table_fields_dct['experiment_iteration'] = f'Exp_iter_{exp_iter_num}'
exp_iter_data_loader = copy.deepcopy(data_loader)  # Add deepcopy to avoid data leakage

In [14]:
run_exp_iter_with_inprocessor(data_loader=exp_iter_data_loader,
                              experiment_seed=experiment_seed,
                              test_set_fraction=TEST_SET_FRACTION,
                              db_writer_func=db_writer_func,
                              fair_intervention_params_lst=FAIR_INTERVENTION_PARAMS_LST,
                              metrics_computation_config=metrics_computation_config,
                              custom_table_fields_dct=custom_table_fields_dct,
                              dataset_name='LawSchoolDataset',
                              inprocessor_name='AdversarialDebiasing',
                              verbose=True)

2024-01-04 20:15:17 experiment_interface.py INFO    : Start an experiment iteration for the following custom params:
INFO:root:Start an experiment iteration for the following custom params:


{'dataset_split_seed': 400,
 'experiment_iteration': 'Exp_iter_4',
 'fair_intervention_params_lst': '[True]',
 'intervention_param': 'True',
 'model_init_seed': 400,
 'session_uuid': '0626d80f-e288-4f16-b8ab-260eb34d62d3'}


Multiple alphas:   0%|          | 0/1 [00:00<?, ?it/s]

2024-01-04 20:15:17 experiment_interface.py INFO    : The dataset is preprocessed
INFO:root:The dataset is preprocessed
2024-01-04 20:15:17 experiment_interface.py INFO    : Models config is loaded from the input file
INFO:root:Models config is loaded from the input file


intervention_option:  True
Using ROC postprocessor
cur_base_flow_dataset.X_train_val.columns:  Index(['cat__school_GP', 'cat__school_MS', 'cat__address_R', 'cat__address_U',
       'cat__famsize_GT3', 'cat__famsize_LE3', 'cat__Pstatus_A',
       'cat__Pstatus_T', 'cat__Mjob_at_home', 'cat__Mjob_health',
       'cat__Mjob_other', 'cat__Mjob_services', 'cat__Mjob_teacher',
       'cat__Fjob_at_home', 'cat__Fjob_health', 'cat__Fjob_other',
       'cat__Fjob_services', 'cat__Fjob_teacher', 'cat__reason_course',
       'cat__reason_home', 'cat__reason_other', 'cat__reason_reputation',
       'cat__guardian_father', 'cat__guardian_mother', 'cat__guardian_other',
       'cat__schoolsup_no', 'cat__schoolsup_yes', 'cat__famsup_no',
       'cat__famsup_yes', 'cat__paid_no', 'cat__paid_yes',
       'cat__activities_no', 'cat__activities_yes', 'cat__nursery_no',
       'cat__nursery_yes', 'cat__higher_no', 'cat__higher_yes',
       'cat__internet_no', 'cat__internet_yes', 'cat__romantic_no',
     

...

[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGB

[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGB

Classifiers testing by bootstrap:   0%|          | 0/200 [00:00<?, ?it/s]

Enabled a postprocessing mode


Classifiers testing by bootstrap:   0%|          | 0/200 [00:00<?, ?it/s]

### Experiment iteration 5

In [11]:
# Configs for an experiment iteration
exp_iter_num = 5
experiment_seed = EXPERIMENT_SEEDS[exp_iter_num - 1]
custom_table_fields_dct['experiment_iteration'] = f'Exp_iter_{exp_iter_num}'
exp_iter_data_loader = copy.deepcopy(data_loader)  # Add deepcopy to avoid data leakage

In [12]:
run_exp_iter_with_inprocessor(data_loader=exp_iter_data_loader,
                              experiment_seed=experiment_seed,
                              test_set_fraction=TEST_SET_FRACTION,
                              db_writer_func=db_writer_func,
                              fair_intervention_params_lst=FAIR_INTERVENTION_PARAMS_LST,
                              metrics_computation_config=metrics_computation_config,
                              custom_table_fields_dct=custom_table_fields_dct,
                              dataset_name='LawSchoolDataset',
                              inprocessor_name='AdversarialDebiasing',
                              verbose=True)

2024-01-05 03:55:49 experiment_interface.py INFO    : Start an experiment iteration for the following custom params:
INFO:root:Start an experiment iteration for the following custom params:


{'dataset_split_seed': 500,
 'experiment_iteration': 'Exp_iter_5',
 'fair_intervention_params_lst': '[True]',
 'model_init_seed': 500,
 'session_uuid': '0626d80f-e288-4f16-b8ab-260eb34d62d3'}


Multiple alphas:   0%|          | 0/1 [00:00<?, ?it/s]

2024-01-05 03:55:49 experiment_interface.py INFO    : The dataset is preprocessed
INFO:root:The dataset is preprocessed
2024-01-05 03:55:49 experiment_interface.py INFO    : Models config is loaded from the input file
INFO:root:Models config is loaded from the input file


intervention_option:  True
Using ROC postprocessor
cur_base_flow_dataset.X_train_val.columns:  Index(['cat__school_GP', 'cat__school_MS', 'cat__address_R', 'cat__address_U',
       'cat__famsize_GT3', 'cat__famsize_LE3', 'cat__Pstatus_A',
       'cat__Pstatus_T', 'cat__Mjob_at_home', 'cat__Mjob_health',
       'cat__Mjob_other', 'cat__Mjob_services', 'cat__Mjob_teacher',
       'cat__Fjob_at_home', 'cat__Fjob_health', 'cat__Fjob_other',
       'cat__Fjob_services', 'cat__Fjob_teacher', 'cat__reason_course',
       'cat__reason_home', 'cat__reason_other', 'cat__reason_reputation',
       'cat__guardian_father', 'cat__guardian_mother', 'cat__guardian_other',
       'cat__schoolsup_no', 'cat__schoolsup_yes', 'cat__famsup_no',
       'cat__famsup_yes', 'cat__paid_no', 'cat__paid_yes',
       'cat__activities_no', 'cat__activities_yes', 'cat__nursery_no',
       'cat__nursery_yes', 'cat__higher_no', 'cat__higher_yes',
       'cat__internet_no', 'cat__internet_yes', 'cat__romantic_no',
     

...

[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGB

[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGB

Classifiers testing by bootstrap:   0%|          | 0/200 [00:00<?, ?it/s]

Enabled a postprocessing mode


Classifiers testing by bootstrap:   0%|          | 0/200 [00:00<?, ?it/s]

### Experiment iteration 6

In [11]:
# Configs for an experiment iteration
exp_iter_num = 6
experiment_seed = EXPERIMENT_SEEDS[exp_iter_num - 1]
custom_table_fields_dct['experiment_iteration'] = f'Exp_iter_{exp_iter_num}'
exp_iter_data_loader = copy.deepcopy(data_loader)  # Add deepcopy to avoid data leakage

In [12]:
run_exp_iter_with_inprocessor(data_loader=exp_iter_data_loader,
                              experiment_seed=experiment_seed,
                              test_set_fraction=TEST_SET_FRACTION,
                              db_writer_func=db_writer_func,
                              fair_intervention_params_lst=FAIR_INTERVENTION_PARAMS_LST,
                              metrics_computation_config=metrics_computation_config,
                              custom_table_fields_dct=custom_table_fields_dct,
                              dataset_name='LawSchoolDataset',
                              inprocessor_name='AdversarialDebiasing',
                              verbose=True)

2024-01-08 21:53:05 experiment_interface.py INFO    : Start an experiment iteration for the following custom params:
INFO:root:Start an experiment iteration for the following custom params:


{'dataset_split_seed': 600,
 'experiment_iteration': 'Exp_iter_6',
 'fair_intervention_params_lst': "['debiased_classifier']",
 'model_init_seed': 600,
 'session_uuid': '594152d2-738f-43f3-87ac-e98b98a17b4a'}




Multiple alphas:   0%|          | 0/1 [00:00<?, ?it/s]

2024-01-08 21:53:05 experiment_interface.py INFO    : The dataset is preprocessed
INFO:root:The dataset is preprocessed


intervention_option:  debiased_classifier
cur_base_flow_dataset.X_train_val.columns:  Index(['cat__fulltime_1.0', 'cat__fulltime_2.0', 'cat__fam_inc_1.0',
       'cat__fam_inc_2.0', 'cat__fam_inc_3.0', 'cat__fam_inc_4.0',
       'cat__fam_inc_5.0', 'cat__tier_1.0', 'cat__tier_2.0', 'cat__tier_3.0',
       'cat__tier_4.0', 'cat__tier_5.0', 'cat__tier_6.0', 'num__decile1b',
       'num__decile3', 'num__lsat', 'num__ugpa', 'num__zfygpa', 'num__zgpa',
       'male&race_binary'],
      dtype='object')
Top indexes of an X_test in the current base flow dataset:  Int64Index([ 9347, 19474, 17223,  1292, 13480,  5501,  2413, 10309,  6657,
            14802,  4565,  5107,  5436, 20504,  5959,  3443, 20524,  4751,
            18806,   198],
           dtype='int64')
Top indexes of an y_test in the current base flow dataset:  Int64Index([ 9347, 19474, 17223,  1292, 13480,  5501,  2413, 10309,  6657,
            14802,  4565,  5107,  5436, 20504,  5959,  3443, 20524,  4751,
            18806,   198]

...

epoch 198; iter: 0; batch classifier loss: 0.144734; batch adversarial loss: 0.300996
epoch 199; iter: 0; batch classifier loss: 0.193683; batch adversarial loss: 0.241381
epoch 0; iter: 0; batch classifier loss: 0.742618; batch adversarial loss: 0.919209
epoch 1; iter: 0; batch classifier loss: 0.271010; batch adversarial loss: 1.019407
epoch 2; iter: 0; batch classifier loss: 0.285144; batch adversarial loss: 0.857521
epoch 3; iter: 0; batch classifier loss: 0.185748; batch adversarial loss: 0.756551
epoch 4; iter: 0; batch classifier loss: 0.192861; batch adversarial loss: 0.666426
epoch 5; iter: 0; batch classifier loss: 0.242794; batch adversarial loss: 0.568729
epoch 6; iter: 0; batch classifier loss: 0.164663; batch adversarial loss: 0.512991
epoch 7; iter: 0; batch classifier loss: 0.224912; batch adversarial loss: 0.464402
epoch 8; iter: 0; batch classifier loss: 0.341567; batch adversarial loss: 0.450781
epoch 9; iter: 0; batch classifier loss: 0.189556; batch adversarial los

epoch 96; iter: 0; batch classifier loss: 0.228724; batch adversarial loss: 0.348847
epoch 97; iter: 0; batch classifier loss: 0.277093; batch adversarial loss: 0.183572
epoch 98; iter: 0; batch classifier loss: 0.144904; batch adversarial loss: 0.304024
epoch 99; iter: 0; batch classifier loss: 0.241053; batch adversarial loss: 0.242433
epoch 100; iter: 0; batch classifier loss: 0.168198; batch adversarial loss: 0.264549
epoch 101; iter: 0; batch classifier loss: 0.297346; batch adversarial loss: 0.271373
epoch 102; iter: 0; batch classifier loss: 0.255026; batch adversarial loss: 0.255923
epoch 103; iter: 0; batch classifier loss: 0.168931; batch adversarial loss: 0.307093
epoch 104; iter: 0; batch classifier loss: 0.243953; batch adversarial loss: 0.203540
epoch 105; iter: 0; batch classifier loss: 0.218963; batch adversarial loss: 0.211009
epoch 106; iter: 0; batch classifier loss: 0.227023; batch adversarial loss: 0.329843
epoch 107; iter: 0; batch classifier loss: 0.204886; batch

epoch 192; iter: 0; batch classifier loss: 0.188893; batch adversarial loss: 0.367555
epoch 193; iter: 0; batch classifier loss: 0.200115; batch adversarial loss: 0.265942
epoch 194; iter: 0; batch classifier loss: 0.197172; batch adversarial loss: 0.360339
epoch 195; iter: 0; batch classifier loss: 0.124797; batch adversarial loss: 0.301700
epoch 196; iter: 0; batch classifier loss: 0.226776; batch adversarial loss: 0.270395
epoch 197; iter: 0; batch classifier loss: 0.194224; batch adversarial loss: 0.221457
epoch 198; iter: 0; batch classifier loss: 0.260211; batch adversarial loss: 0.313262
epoch 199; iter: 0; batch classifier loss: 0.317637; batch adversarial loss: 0.327515
epoch 0; iter: 0; batch classifier loss: 0.696116; batch adversarial loss: 0.516177
epoch 1; iter: 0; batch classifier loss: 0.500193; batch adversarial loss: 0.465853
epoch 2; iter: 0; batch classifier loss: 0.635997; batch adversarial loss: 0.428159
epoch 3; iter: 0; batch classifier loss: 1.249248; batch adv

epoch 90; iter: 0; batch classifier loss: 0.156597; batch adversarial loss: 0.301489
epoch 91; iter: 0; batch classifier loss: 0.134659; batch adversarial loss: 0.288730
epoch 92; iter: 0; batch classifier loss: 0.218930; batch adversarial loss: 0.288898
epoch 93; iter: 0; batch classifier loss: 0.184083; batch adversarial loss: 0.245399
epoch 94; iter: 0; batch classifier loss: 0.183403; batch adversarial loss: 0.259025
epoch 95; iter: 0; batch classifier loss: 0.299851; batch adversarial loss: 0.290871
epoch 96; iter: 0; batch classifier loss: 0.285070; batch adversarial loss: 0.299305
epoch 97; iter: 0; batch classifier loss: 0.212139; batch adversarial loss: 0.228611
epoch 98; iter: 0; batch classifier loss: 0.235702; batch adversarial loss: 0.322940
epoch 99; iter: 0; batch classifier loss: 0.145792; batch adversarial loss: 0.212191
epoch 100; iter: 0; batch classifier loss: 0.243789; batch adversarial loss: 0.270376
epoch 101; iter: 0; batch classifier loss: 0.154284; batch adver

epoch 186; iter: 0; batch classifier loss: 0.189992; batch adversarial loss: 0.234860
epoch 187; iter: 0; batch classifier loss: 0.217690; batch adversarial loss: 0.306491
epoch 188; iter: 0; batch classifier loss: 0.266328; batch adversarial loss: 0.277260
epoch 189; iter: 0; batch classifier loss: 0.142849; batch adversarial loss: 0.315722
epoch 190; iter: 0; batch classifier loss: 0.224658; batch adversarial loss: 0.284569
epoch 191; iter: 0; batch classifier loss: 0.156239; batch adversarial loss: 0.308352
epoch 192; iter: 0; batch classifier loss: 0.173827; batch adversarial loss: 0.294342
epoch 193; iter: 0; batch classifier loss: 0.129387; batch adversarial loss: 0.253759
epoch 194; iter: 0; batch classifier loss: 0.151418; batch adversarial loss: 0.216928
epoch 195; iter: 0; batch classifier loss: 0.158435; batch adversarial loss: 0.292022
epoch 196; iter: 0; batch classifier loss: 0.256732; batch adversarial loss: 0.232700
epoch 197; iter: 0; batch classifier loss: 0.229990; b